In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
from matplotlib import pyplot as plt

In [145]:
train = pd.read_csv('../../input/train_V2.csv')
test = pd.read_csv('../../input/test_V2.csv')

In [146]:
group_lvl_features = pd.read_csv('../../input/groupLevelFeatures_train.csv')
group_lvl_features_test = pd.read_csv('../../input/groupLevelFeatures_test.csv')

In [4]:
def compute_dcg(ordered_relevance):
    
    dcg = 0
    for i in range(len(ordered_relevance)):
        numerator = ordered_relevance[i,1]
        denomenator = np.log2(i + 2)
        dcg += numerator/denomenator
        
        
    return dcg

def ndcg(match_expectations, match_predictions, rank=None): 
    a = match_expectations.reshape(len(match_expectations),1)
    b = match_predictions.reshape(len(match_predictions),1)
    combined_values = np.hstack((a,b))
    
    ordered_relevance = combined_values[combined_values[:,0].argsort()[::-1]]    
    dcg = compute_dcg(combined_values)
    
    ideal_combination = np.hstack((a,a))
    idcg = compute_dcg(ideal_combination)
    
    return dcg/idcg
        
    

## Make sure the prediction output order is similar to data input order.
ndcg(np.array([3,3,3,2,2,2]),np.array([4,3,3,2,2,2]))

1.1144130414141749

In [5]:
def getWinPlacePerc(dataset, predictions):
    concatenated = pd.concat([dataset.reset_index(), pd.DataFrame({'Predicted': predictions})], axis=1)    
    concatenated['rank'] = concatenated.groupby('matchId')['Predicted'].rank(method='dense')
    concatenated['pr_winPlacePerc'] = (concatenated['rank'] - 1) / (concatenated['maxPlace'] - 1)
    return concatenated

In [6]:
feature_list = group_lvl_features.columns[2:]

In [7]:
from sklearn.preprocessing import MinMaxScaler
scaler = MinMaxScaler()

X = group_lvl_features
y = pd.merge(group_lvl_features,train[['groupId','maxPlace','winPlacePerc']], on='groupId', how='inner').drop_duplicates().reset_index()
# y = group_lvl_features.merge(train[['groupId','maxPlace','winPlacePerc']], on='groupId', how='inner').drop_duplicates().reset_index()
y['winPlacePerc'] = y['winPlacePerc'].fillna(0)

In [10]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(train_by_match, y_by_match, test_size=0.33, random_state=42)

In [64]:
train_by_match = X_train.groupby('matchId').agg({f: (lambda x: x.tolist()) for f in X_train.columns[1:]})
test_by_match = X_test.groupby('matchId').agg({f: (lambda x: x.tolist()) for f in X_train.columns[1:]})

# train_by_match = X_train.groupby('matchId').agg({f: 'sum' for f in X_train.columns[1:]})
# test_by_match = X_test.groupby('matchId').agg({f: 'sum' for f in X_train.columns[1:]})

In [65]:
train_labels_per_match = y.groupby('matchId').agg({'groupId': (lambda x: x.tolist()),
                                                            'winPlacePerc': (lambda x: x.tolist())})
test_labels_per_match = y_test.groupby('matchId').agg({'groupId': (lambda x: x.tolist()),
                                                            'winPlacePerc': (lambda x: x.tolist())})

In [11]:
X_train[X_train.columns.intersection(feature_list)] = scaler.fit_transform(X_train[X_train.columns.intersection(feature_list)])

/miniconda2/envs/AML/lib/python3.6/site-packages/sklearn/preprocessing/data.py:323: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by MinMaxScaler.
  return self.partial_fit(X, y)
/miniconda2/envs/AML/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.
/miniconda2/envs/AML/lib/python3.6/site-packages/pandas/core/indexing.py:543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


In [12]:
X_test[X_train.columns.intersection(feature_list)] = scaler.transform(X_test[X_train.columns.intersection(feature_list)])

/miniconda2/envs/AML/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.
/miniconda2/envs/AML/lib/python3.6/site-packages/pandas/core/indexing.py:543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


In [92]:
# import autograd.numpy as anp
# from autograd import grad
import copy
import time
# from sklearn.linear_model import LinearRegression 

class LinearNDCGRegression:
    
    def _get_match(self, index, d2array):
        return np.array([x for x in d2array.iloc[index][1:]])
                
    '''
        Computing the gradients in a naive way, i.e. limiting differences.
    '''
    def _grad(self, b, w, train_per_match, labels_per_match):
        e = 1e-2
        gradW = np.zeros(w.shape)
        gradB = (self._loss_function(b + e,w, train_per_match, labels_per_match) - self._loss_function(b - e,w, train_per_match, labels_per_match)) / (2 * e) 
        
        for wIndex in range(len(self.w)):
            w_copy1 = copy.deepcopy(self.w)
            w_copy2 = copy.deepcopy(self.w)
            w_copy1[wIndex] += e
            w_copy2[wIndex] -= e

            gradW[wIndex] = (self._loss_function(b,w_copy1, train_per_match, labels_per_match) - self._loss_function(b,w_copy2, train_per_match, labels_per_match)) / (2 * e) 
        
        return gradW, gradB
        
    '''
        Compute the Sum of Squared Errors of all matches.         
        Current approach: computing the SSE per match and summing that to the sum of all match SSEs.
    '''
    def _loss_function(self, b, w, train_per_match, labels_per_match):
        SSE = 0
        
        for matchIndex in range(train_per_match.shape[0]):

            current_match = train_per_match.iloc[matchIndex].name
    
            match = self._get_match(matchIndex, train_per_match)
            
            maxPlace = match.shape[1]
            if maxPlace == 1:
                continue
        
            match_labels = self._get_match(matchIndex, labels_per_match)
            predictions = self._predict(match, b,w)
            
            if (self.loss == 'sse'):
                SSE += np.sum(np.power((predictions - match_labels[0]),2))  
            else:
                SSE += ndcg(match_labels[0],predictions)
            
        return SSE

    '''
        Param@ match is N X M numpy array, where M is the number of groups participating in a match
    ''' 
    def _predict(self, match, b, w):
        
        maxPlace = match.shape[1]
        if maxPlace == 1:
            return 1
        linear_pred = np.dot(match.T, w) + b

        ranks = linear_pred.argsort().argsort()
        predictions = ranks / (maxPlace - 1)
        
        return np.around(predictions,4)
    
    '''
        Public function for predicting
    '''
    def predict(self, match):
        return self._predict(match, self.b, self.w)
    
    '''
        Initialize class by creating N random weights
    '''
    def fit(self, train_by_match, labels_by_match, loss='sse', num_iter=100):
        self.loss = loss
        
        shape = train_by_match.shape
        N = shape[1] - 1
        self.b = np.random.rand(1)[0]
        self.w = np.random.rand(N)
        
        learning_rate = 1e-3
        old_cost = self._loss_function(self.b,self.w, train_by_match, labels_by_match)
#         return
        for i in range(num_iter):
            time1 = time.time()
            gradW, gradB = self._grad(self.b, self.w, train_by_match, labels_by_match)
            newW = self.w - learning_rate * gradW
            newB = self.b - learning_rate * gradB
            new_cost = self._loss_function(self.b,self.w, train_by_match, labels_by_match)
            
            while (new_cost - old_cost > 0):
                print("Decreasing learning rate!")
                ## the cost is increasing, decrease learning rate
                learning_rate -= 1e-4
                ## and recompute grad
                gradW, gradB = self._grad(self.b, self.w, train_by_match, labels_by_match)
                newW = self.w - learning_rate * gradW
                newB = self.b - learning_rate * gradB
                new_cost = self._loss_function(self.b,self.w, train_by_match, labels_by_match)
            
            self.w = newW
            self.b = newB
            time2 = time.time()
            print("Iteration {}: Current train loss: {}, {}s ".format(i+1, new_cost,np.around(time2 - time1,2)))
            
        return self
        
    def get_params(self):
        return self.b,self.w
        
        

In [97]:
train_by_match.to_pickle('train_by_match.zip')
test_by_match.to_pickle('test_by_match.zip')

In [98]:
train_labels_per_match.to_pickle('train_labels_per_match.zip')
test_labels_per_match.to_pickle('test_labels_per_match.zip')

In [182]:
fitted_model2 = LinearNDCGRegression().fit(train_by_match.iloc[:20],train_labels_per_match.iloc[:20])

Iteration 1: Current train loss: 99.20655377


KeyboardInterrupt: 

In [96]:
# It takes 18 seconds for 1 learning iteration with a 100 samples of data
# All samples will therefore take, about, 864 seconds for 1 iterations, which is about 15 minutes per iteration.
fitted_model = LinearNDCGRegression().fit(train_by_match.iloc[:200],train_labels_per_match, num_iter=30)

Iteration 1: Current train loss: 1003.1469444200003, 36.56s 
Iteration 2: Current train loss: 413.75444448000036, 36.06s 
Iteration 3: Current train loss: 215.17975260000006, 36.26s 
Iteration 4: Current train loss: 206.36620843999995, 36.26s 
Iteration 5: Current train loss: 201.68811094000003, 36.18s 
Iteration 6: Current train loss: 195.84101020000003, 36.21s 
Iteration 7: Current train loss: 186.47350909999994, 37.01s 
Iteration 8: Current train loss: 179.79020223999999, 35.99s 
Iteration 9: Current train loss: 172.53645210000005, 38.64s 
Iteration 10: Current train loss: 167.28113676000007, 36.86s 
Iteration 11: Current train loss: 164.02830166, 36.8s 
Iteration 12: Current train loss: 161.33161833999986, 36.0s 
Iteration 13: Current train loss: 158.86972174000002, 36.09s 
Iteration 14: Current train loss: 154.7721973400002, 36.55s 
Iteration 15: Current train loss: 151.95000852000004, 36.42s 
Iteration 16: Current train loss: 149.68190528000002, 36.69s 
Iteration 17: Current trai

In [178]:
# by_match_predictions = np.array([])
sae = 0
sndcg = 0

for matchIndex in range(test_by_match.shape[0]):
        current_match = test_by_match.iloc[matchIndex].name

        match = fitted_model._get_match(matchIndex, test_by_match)
        
        if match.shape[1] == 1:
            continue
            
        match_labels = fitted_model._get_match(matchIndex, test_labels_per_match)
        predictions = fitted_model._predict(match, params[0],params[1])
        
        mean_absolute_error = np.sum(np.abs(predictions - match_labels[0])) / match.shape[1]
        print(mean_absolute_error)
        sndcg += ndcg(match_labels[0],predictions)
        sae += mean_absolute_error
        print("{}: Current mae: {}, current mndcg: {}".format(matchIndex,sae/matchIndex, sndcg/matchIndex))
        
#         if len(by_match_predictions) == 0:
#             by_match_predictions = np.array([predictions])
#         else:
#             by_match_predictions = np.append(by_match_predictions,predictions,axis=0)
            
#         print(by_match_predictions)
        
mae = sae / test_by_match.shape[0]
mndcg = sndcg / test_by_match.shape[0]

0.10618333333333331
0: Current mae: inf, current mndcg: inf
[[0.2 0.4 0.  0.8 1.  0.6]]
0.18913750000000001
1: Current mae: 0.2953208333333333, current mndcg: 1.7528214762544576
[[0.2 0.4 0.  0.8 1.  0.6]]
0.081068
2: Current mae: 0.18819441666666664, current mndcg: 1.3812255628609975
[[0.2 0.4 0.  0.8 1.  0.6]]
0.05917333333333333
3: Current mae: 0.14518738888888885, current mndcg: 1.2723390542520472
[[0.2 0.4 0.  0.8 1.  0.6]]
0.14365624999999999
4: Current mae: 0.14480460416666663, current mndcg: 1.196522228452564
[[0.2 0.4 0.  0.8 1.  0.6]]
0.13055714285714284
5: Current mae: 0.14195511190476187, current mndcg: 1.1903878860593766
[[0.2 0.4 0.  0.8 1.  0.6]]
0.12008823529411765
6: Current mae: 0.1383106324696545, current mndcg: 1.142599692041917
[[0.2 0.4 0.  0.8 1.  0.6]]
0.060835135135135124
7: Current mae: 0.12724270427900888, current mndcg: 1.1290138198812325
[[0.2 0.4 0.  0.8 1.  0.6]]
0.14441538461538464
8: Current mae: 0.12938928932105584, current mndcg: 1.1209953964226385
[[

/miniconda2/envs/AML/lib/python3.6/site-packages/ipykernel_launcher.py:20: RuntimeWarning: divide by zero encountered in double_scalars


0.13072162162162163
143: Current mae: 0.1400829287186023, current mndcg: 1.069239152018817
[[0.2 0.4 0.  0.8 1.  0.6]]
0.10137
144: Current mae: 0.13981408893583425, current mndcg: 1.0682401796699632
[[0.2 0.4 0.  0.8 1.  0.6]]
0.06867500000000001
145: Current mae: 0.1393234745293802, current mndcg: 1.067732874349523
[[0.2 0.4 0.  0.8 1.  0.6]]
0.1508142857142857
146: Current mae: 0.1394021787155782, current mndcg: 1.0663066924921327
[[0.2 0.4 0.  0.8 1.  0.6]]
0.1679923076923077
147: Current mae: 0.1395966693888893, current mndcg: 1.0642230787261249
[[0.2 0.4 0.  0.8 1.  0.6]]
0.117452
148: Current mae: 0.13944704324436977, current mndcg: 1.0641501461170855
[[0.2 0.4 0.  0.8 1.  0.6]]
0.14137272727272732
149: Current mae: 0.13945996729825136, current mndcg: 1.0629280520777113
[[0.2 0.4 0.  0.8 1.  0.6]]
0.09870000000000001
150: Current mae: 0.1391882341829297, current mndcg: 1.0617037753180036
[[0.2 0.4 0.  0.8 1.  0.6]]
0.22223333333333337
151: Current mae: 0.13973820172697207, curre

0.21743333333333334
285: Current mae: 0.14037674769229902, current mndcg: 1.0356321909973805
[[0.2 0.4 0.  0.8 1.  0.6]]
0.19166
286: Current mae: 0.14055605976330496, current mndcg: 1.0355409463718195
[[0.2 0.4 0.  0.8 1.  0.6]]
0.10740000000000001
287: Current mae: 0.14044053342266627, current mndcg: 1.034980155061064
[[0.2 0.4 0.  0.8 1.  0.6]]
0.14470000000000002
288: Current mae: 0.14045532323717091, current mndcg: 1.0343213554777808
[[0.2 0.4 0.  0.8 1.  0.6]]
0.08273125
289: Current mae: 0.14025558595953364, current mndcg: 1.0340986368418652
[[0.2 0.4 0.  0.8 1.  0.6]]
0.1583333333333333
290: Current mae: 0.1403179230194433, current mndcg: 1.0339671126196424
[[0.2 0.4 0.  0.8 1.  0.6]]
0.1490375
291: Current mae: 0.14034788720150704, current mndcg: 1.0334771401861578
[[0.2 0.4 0.  0.8 1.  0.6]]
0.09370909090909088
292: Current mae: 0.14018816529639605, current mndcg: 1.0333290387719103
[[0.2 0.4 0.  0.8 1.  0.6]]
0.07855
293: Current mae: 0.13997779613156194, current mndcg: 1.03

0.1035090909090909
419: Current mae: 0.13688853475225787, current mndcg: 1.0250919346879297
[[0.2 0.4 0.  0.8 1.  0.6]]
0.1389
420: Current mae: 0.13689332395522869, current mndcg: 1.0248552377260167
[[0.2 0.4 0.  0.8 1.  0.6]]
0.10308965517241381
421: Current mae: 0.13681303020515073, current mndcg: 1.0248428405281695
[[0.2 0.4 0.  0.8 1.  0.6]]
0.11482
422: Current mae: 0.13676091401983048, current mndcg: 1.0253546919118044
[[0.2 0.4 0.  0.8 1.  0.6]]
0.15800344827586205
423: Current mae: 0.13681113277693693, current mndcg: 1.0250872552903683
[[0.2 0.4 0.  0.8 1.  0.6]]
0.09432857142857144
424: Current mae: 0.1367109380567757, current mndcg: 1.025324445086602
[[0.2 0.4 0.  0.8 1.  0.6]]
0.13174615384615387
425: Current mae: 0.13669925621157422, current mndcg: 1.0251245368396453
[[0.2 0.4 0.  0.8 1.  0.6]]
0.06833
426: Current mae: 0.13653876499980996, current mndcg: 1.0253179844697378
[[0.2 0.4 0.  0.8 1.  0.6]]
0.1643
427: Current mae: 0.13660377960168393, current mndcg: 1.025110366

...

[[0.2 0.4 0.  0.8 1.  0.6]]
0.06482222222222223
46881: Current mae: 0.13584014588371424, current mndcg: 1.023019329280903
[[0.2 0.4 0.  0.8 1.  0.6]]
0.11198999999999999
46882: Current mae: 0.13583963715657196, current mndcg: 1.02302169152027
[[0.2 0.4 0.  0.8 1.  0.6]]
0.26380000000000003
46883: Current mae: 0.13584236651183598, current mndcg: 1.0230170446091658
[[0.2 0.4 0.  0.8 1.  0.6]]
0.14446
46884: Current mae: 0.13584255031939269, current mndcg: 1.0230154814667518
[[0.2 0.4 0.  0.8 1.  0.6]]
0.13608333333333333
46885: Current mae: 0.1358425554550014, current mndcg: 1.0230193596786017
[[0.2 0.4 0.  0.8 1.  0.6]]
0.11417142857142859
46886: Current mae: 0.13584209324609292, current mndcg: 1.0230142522844736
[[0.2 0.4 0.  0.8 1.  0.6]]
0.13302666666666668
46887: Current mae: 0.13584203319903126, current mndcg: 1.0230141410610551
[[0.2 0.4 0.  0.8 1.  0.6]]
0.11643749999999997
46888: Current mae: 0.13584161935043035, current mndcg: 1.0230151527475846
[[0.2 0.4 0.  0.8 1.  0.6]]
0.17

0.12064999999999997
47047: Current mae: 0.13582028016314746, current mndcg: 1.0229913612985009
[[0.2 0.4 0.  0.8 1.  0.6]]
0.11904999999999999
47048: Current mae: 0.13581992371271037, current mndcg: 1.0229875639564845
[[0.2 0.4 0.  0.8 1.  0.6]]
0.2289916666666667
47049: Current mae: 0.13582190402563848, current mndcg: 1.0229902175099461
[[0.2 0.4 0.  0.8 1.  0.6]]
0.09943333333333333
47050: Current mae: 0.13582113062349838, current mndcg: 1.0229898824323767
[[0.2 0.4 0.  0.8 1.  0.6]]
0.13095555555555555
47051: Current mae: 0.13582102721283615, current mndcg: 1.0229891444237724
[[0.2 0.4 0.  0.8 1.  0.6]]
0.09327857142857139
47052: Current mae: 0.1358201230545478, current mndcg: 1.022989675566302
[[0.2 0.4 0.  0.8 1.  0.6]]
0.1276529411764706
47053: Current mae: 0.1358199494804531, current mndcg: 1.022985295337067
[[0.2 0.4 0.  0.8 1.  0.6]]
0.11751999999999999
47054: Current mae: 0.13581956056666294, current mndcg: 1.0229832832044574
[[0.2 0.4 0.  0.8 1.  0.6]]
0.1532
47055: Current 

0.10604090909090907
47237: Current mae: 0.13579302745457592, current mndcg: 1.0230283460458085
[[0.2 0.4 0.  0.8 1.  0.6]]
0.0879
47238: Current mae: 0.13579201358803936, current mndcg: 1.0230280435491146
[[0.2 0.4 0.  0.8 1.  0.6]]
0.14471052631578948
47239: Current mae: 0.1357922023835839, current mndcg: 1.0230331392223766
[[0.2 0.4 0.  0.8 1.  0.6]]
0.14218000000000003
47240: Current mae: 0.13579233760368584, current mndcg: 1.0230304090296702
[[0.2 0.4 0.  0.8 1.  0.6]]
0.1250571428571429
47241: Current mae: 0.1357921103605126, current mndcg: 1.0230305411588654
[[0.2 0.4 0.  0.8 1.  0.6]]
0.10628333333333333
47242: Current mae: 0.1357914857303736, current mndcg: 1.0230302810190632
[[0.2 0.4 0.  0.8 1.  0.6]]
0.09595555555555554
47243: Current mae: 0.13579064251698378, current mndcg: 1.0230257050172857
[[0.2 0.4 0.  0.8 1.  0.6]]
0.11213333333333335
47244: Current mae: 0.13579014176960458, current mndcg: 1.0230237006315097
[[0.2 0.4 0.  0.8 1.  0.6]]
0.18711818181818182
47245: Curren

0.19286666666666666
47383: Current mae: 0.13580045114117228, current mndcg: 1.0230173813721588
[[0.2 0.4 0.  0.8 1.  0.6]]
0.14916666666666667
47384: Current mae: 0.13580073322405947, current mndcg: 1.0230140700462875
[[0.2 0.4 0.  0.8 1.  0.6]]
0.10135454545454543
47385: Current mae: 0.13580000628119213, current mndcg: 1.0230128292157186
[[0.2 0.4 0.  0.8 1.  0.6]]
0.1762
47386: Current mae: 0.1358008588535493, current mndcg: 1.023006262702066
[[0.2 0.4 0.  0.8 1.  0.6]]
0.056639130434782615
47387: Current mae: 0.13579918831672658, current mndcg: 1.0230046911489006
[[0.2 0.4 0.  0.8 1.  0.6]]
0.17341
47388: Current mae: 0.13579998199469745, current mndcg: 1.0230054886995927
[[0.2 0.4 0.  0.8 1.  0.6]]
0.18149999999999997
47389: Current mae: 0.13580094635389484, current mndcg: 1.0230049060317363
[[0.2 0.4 0.  0.8 1.  0.6]]
0.12890000000000001
47390: Current mae: 0.13580080073358772, current mndcg: 1.023005138225861
[[0.2 0.4 0.  0.8 1.  0.6]]
0.15872222222222224
47391: Current mae: 0.1

[[0.2 0.4 0.  0.8 1.  0.6]]
0.2033
47550: Current mae: 0.13582097772486557, current mndcg: 1.0229880976417471
[[0.2 0.4 0.  0.8 1.  0.6]]
0.17142857142857146
47551: Current mae: 0.13582172655441077, current mndcg: 1.0229902647336295
[[0.2 0.4 0.  0.8 1.  0.6]]
0.2032857142857143
47552: Current mae: 0.13582314529574094, current mndcg: 1.0229848611803114
[[0.2 0.4 0.  0.8 1.  0.6]]
0.07106666666666667
47553: Current mae: 0.135821783520908, current mndcg: 1.022984036712706
[[0.2 0.4 0.  0.8 1.  0.6]]
0.04887058823529413
47554: Current mae: 0.13581995504811317, current mndcg: 1.0229828804492518
[[0.2 0.4 0.  0.8 1.  0.6]]
0.13678636363636362
47555: Current mae: 0.1358199753700265, current mndcg: 1.0229889975916466
[[0.2 0.4 0.  0.8 1.  0.6]]
0.09597272727272727
47556: Current mae: 0.13581913746843477, current mndcg: 1.0229859914055381
[[0.2 0.4 0.  0.8 1.  0.6]]
0.13617142857142858
47557: Current mae: 0.13581914487620023, current mndcg: 1.0229854829277727
[[0.2 0.4 0.  0.8 1.  0.6]]
0.0871

In [148]:
group_lvl_features_test[group_lvl_features_test.columns.intersection(feature_list)] = scaler.transform(group_lvl_features_test[group_lvl_features_test.columns.intersection(feature_list)])

In [151]:
submiss_by_match = group_lvl_features_test.groupby('matchId').agg({f: (lambda x: x.tolist()) for f in group_lvl_features_test.columns[1:]})

In [190]:
by_match_predictions = {}

for matchIndex in range(submiss_by_match.shape[0]):
        current_match = submiss_by_match.iloc[matchIndex].name
        
        match = fitted_model._get_match(matchIndex, submiss_by_match)
        
        if match.shape[1] == 1:
            continue
            
        match_labels = fitted_model._get_match(matchIndex, test_labels_per_match)
        predictions = fitted_model._predict(match, params[0],params[1])
        
        for i in range(match.shape[1]):
            groupId = submiss_by_match.iloc[matchIndex]['groupId'][i]
            groupPrediction = predictions[i]
            by_match_predictions[groupId] = groupPrediction
            
#         if matchIndex > 10:
#             break
        
submission_by_group_predictions = pd.DataFrame.from_dict(by_match_predictions, orient='index')

In [191]:
submission_by_group_predictions.to_csv('submission_groups.csv')